# Custom Raster Gen for LD2DAPs

In [ ]:
import sys
import numpy as np
import matplotlib.pyplot as plt

sys.path.append("..")
import rasterizer
import raster_assistant as ra

sys.path.append('../triskele/python/')
import triskele

figsize = np.array((16, 3)) * 1.5

## Load LAS data

In [ ]:
C1 = ra.bulk_load('../Data/lidar/C1', 'C1', filter_treshold=.5, dtype=np.float32)
C2 = ra.bulk_load('../Data/lidar/C2', 'C2', filter_treshold=.5, dtype=np.float32)
C3 = ra.bulk_load('../Data/lidar/C3', 'C3', filter_treshold=.5, dtype=np.float32)
C123 = ra.bulk_load('../Data/lidar', 'C123', filter_treshold=.5, dtype=np.float32)

## Raster Validation

### Rasterize some data

In [ ]:
raster = rasterizer.rasterize(C1.spatial, C1.intensity, 0.5, dtype=np.float32)

In [ ]:
plt.figure(figsize=figsize)
plt.imshow(raster, origin='upper')
plt.show()
plt.imsave('../Res/raster_validation.png', raster)

In [ ]:
plt.hist(raster.flatten(), bins=1000)
plt.show()

### Write TIFF file

In [ ]:
triskele.write('../Res/validation.tiff', raster)

### Compare with DFC dataset

In [ ]:
dfc = triskele.read('../Data/phase1_rasters/Intensity_C1/UH17_GI1F051_TR.tif')
our = triskele.read('../Res/validation.tiff')

#### Filter DFC with same parameters

In [ ]:
ra.auto_filter(dfc, treshold=0.5)

#### Display Stats

In [ ]:
dfc.shape, our.shape

In [ ]:
dfc.dtype, our.dtype

In [ ]:
plt.hist(dfc.flatten(), bins=1000, label='DFC')
plt.hist(our.flatten(), bins=1000, label='Our', alpha=.8)
plt.legend()
plt.show()

#### Display Rasters

In [ ]:
f, axs = plt.subplots(2, figsize=figsize * 2)

axs[0].imshow(dfc)
axs[0].set_title('DFC')
axs[1].imshow(our)
axs[1].set_title('Our')

plt.show()

## Raster Pack

In [ ]:
C123.name

In [ ]:
from multiprocessing import Pool, Process, Queue
import multiprocessing as mp
#mp.set_start_method('spawn')

def rasterize_cache_mp(data_var, field, res, method, reverse, cache):
    if data_var == 'C1':
        ra.rasterize_cache(C1, field, res, method, reverse, cache)
    if data_var == 'C2':
        ra.rasterize_cache(C2, field, res, method, reverse, cache)
    if data_var == 'C3':
        ra.rasterize_cache(C3, field, res, method, reverse, cache)
    if data_var == 'C123':
        ra.rasterize_cache(C123, field, res, method, reverse, cache)
    
pool = Pool(processes=5)

job_args = list()

for res in (0.5, 1., 2., 3., 5., 10., .1):
    for reverse in (False, True):
        for inter in ('linear', 'nearest'):
            for field in ('z', 'intensity', 'num_returns'):
                for data in ('C1', 'C2', 'C3', 'C123'):
                    job_args.append([data, field, res, inter, reverse, '../Res/HVR/'])
                    
for i in pool.starmap(rasterize_cache_mp, job_args):
    pass